In [ ]:
  %tensorflow_version 1.x 

TensorFlow 1.x selected.


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
!pip install keras==2.1.6

In [ ]:
!pip install emoji

In [ ]:
!pip install ekphrasis

In [ ]:
pip install plotly==4.5.4

In [ ]:
import numpy as np
import pandas as pd
import string
from nltk.corpus import stopwords
import re
import os

from ekphrasis.classes.preprocessor import TextPreProcessor
from ekphrasis.classes.tokenizer import SocialTokenizer
from ekphrasis.dicts.emoticons import emoticons

In [ ]:
text_processor = TextPreProcessor(
    # terms that will be normalized
    normalize=['url', 'email', 'percent', 'money', 'phone', 'user',
        'time', 'url', 'date', 'number'],
    # terms that will be annotated
    annotate={"hashtag", "allcaps", "elongated", "repeated",
        'emphasis', 'censored'},
    fix_html=True,  # fix HTML tokens
    
    # corpus from which the word statistics are going to be used 
    # for word segmentation 
    segmenter="twitter", 
    
    # corpus from which the word statistics are going to be used 
    # for spell correction
    corrector="twitter", 
    
    unpack_hashtags=True,  # perform word segmentation on hashtags
    unpack_contractions=True,  # Unpack contractions (can't -> can not)
    spell_correct_elong=True,  # spell correction for elongated words
    
    # select a tokenizer. You can use SocialTokenizer, or pass your own
    # the tokenizer, should take as input a string and return a list of tokens
    tokenizer=SocialTokenizer(lowercase=True).tokenize,
    
    # list of dictionaries, for replacing tokens extracted from the text,
    # with other expressions. You can pass more than one dictionaries.
    dicts=[emoticons]
)

In [ ]:
def print_text(texts,i,j):
    for u in range(i,j):
        print(texts[u])
        print()

In [ ]:
df = pd.read_csv('/content/drive/My Drive/offenseval/olid-training-v1.0.tsv',delimiter='\t',encoding='utf-8')
print(list(df.columns.values)) #file header
print(df.head(5)) #last N rows

In [ ]:
df.replace(np.NaN, 'NA', inplace=True)

In [ ]:
df.head(5)

In [ ]:
text_array = df["tweet"]
labels = df["subtask_a"]
labels_target = df["subtask_b"]
print(len(text_array))
print_text(text_array,0,10)

In [ ]:
original = text_array

In [ ]:
from collections import Counter

In [ ]:
df_val_labels_b = pd.read_csv('/content/drive/My Drive/offenseval/labels-levelb.csv', header=None)
print(len(df_val_labels_b))
lol = df_val_labels_b[1]
print(Counter(lol))
df_val_labels_b.head(5)

In [ ]:
labels_target_val = []

In [ ]:
df_val_text = pd.read_csv('/content/drive/My Drive/offenseval/testset-levela.tsv',delimiter='\t',encoding='utf-8')
print(list(df_val_text.columns.values)) #file header
print(df_val_text.head(5)) #first N rows

df_val_labels = pd.read_csv('/content/drive/My Drive/offenseval/labels-levela.csv', header=None)
print(list(df_val_labels.columns.values))
print(df_val_labels.head(5))

count = 0
j = 0
for i in range(0,len(df_val_text["id"])):
    if df_val_labels[1][i] == "OFF":
        if df_val_labels[0][i] == df_val_labels_b[0][j]:
            labels_target_val.append(df_val_labels_b[1][j])
            j = j + 1
    else:
        labels_target_val.append("NA")

print(len(df_val_text["id"]))        
print(count)

text_array_val = df_val_text["tweet"]
labels_val = df_val_labels[1]
print("Checking length of validation set")
print(len(text_array_val),len(labels_val))

In [ ]:
original_val = text_array_val

In [ ]:
Counter(labels_target_val)

In [ ]:
#removing website names
def remove_website(text):
    return " ".join([word if re.search("r'https?://\S+|www\.\S+'|((?i).com$|.co|.net)",word)==None else "" for word in text.split(" ") ])

# Training set 
text_array = text_array.apply(lambda text: remove_website(text))
print_text(text_array,0,10)

print("**************************************************************************")

# Validation set 
text_array_val = text_array_val.apply(lambda text: remove_website(text))
print_text(text_array_val,0,10)

In [ ]:
# Functions for chat word conversion
f = open("/content/drive/My Drive/offenseval/slang.txt", "r")
chat_words_str = f.read()
chat_words_map_dict = {}
chat_words_list = []

for line in chat_words_str.split("\n"):
    if line != "":
        cw = line.split("=")[0]
        cw_expanded = line.split("=")[1]
        chat_words_list.append(cw)
        chat_words_map_dict[cw] = cw_expanded
chat_words_list = set(chat_words_list)

def chat_words_conversion(text):
    new_text = []
    for w in text.split():
        if w.upper() in chat_words_list:
            new_text.append(chat_words_map_dict[w.upper()])
        else:
            new_text.append(w)
    return " ".join(new_text)

In [ ]:
# Chat word conversion
# Training set
text_array = text_array.apply(lambda text: chat_words_conversion(text))
print_text(text_array,0,10)
print_text(original,0,10)

print("********************************************************************************")

# Validation set
text_array_val = text_array_val.apply(lambda text: chat_words_conversion(text))
print_text(text_array_val,0,10)

In [ ]:
os.chdir("/content/drive/My Drive/offenseval")
print(os.getcwd())

In [ ]:
#Function for emoticon conversion
from emoticons import EMOTICONS

def convert_emoticons(text):
    for emot in EMOTICONS:
        text = re.sub(u'('+emot+')', " ".join(EMOTICONS[emot].replace(",","").split()), text)
    return text


#testing the emoticon function
text = "Hello :-) :-)"
text = convert_emoticons(text)
print(text + "\n")

In [ ]:
# Emoticon conversion
# Training set
text_array = text_array.apply(lambda text: convert_emoticons(text))
print_text(text_array,0,10)

print("**********************************************************************************")

# Validation set
text_array_val = text_array_val.apply(lambda text: convert_emoticons(text))
print_text(text_array_val,0,10)

In [ ]:
# FUnction for removal of emoji
import emoji

def convert_emojis(text):
    text = emoji.demojize(text, delimiters=(" ", " "))
    text = re.sub("_|-"," ",text)
    return text

# Training set
text_array = text_array.apply(lambda text: convert_emojis(text))
print_text(text_array,0,10)

print("**************************************************************************")

# Validation set
text_array_val = text_array_val.apply(lambda text: convert_emojis(text))
print_text(text_array_val,0,10)

In [ ]:
os.chdir("/content")
print(os.getcwd())

In [ ]:
# Ekphrasis pipe for text pre-processing
def ekphrasis_pipe(sentence):
    cleaned_sentence = " ".join(text_processor.pre_process_doc(sentence))
    return cleaned_sentence

# Training set
text_array = text_array.apply(lambda text: ekphrasis_pipe(text))
print("Training set completed.......")
#Validation set
text_array_val = text_array_val.apply(lambda text: ekphrasis_pipe(text))
print("Test set completed.......")

In [ ]:
print_text(text_array,0,10)
print("************************************************************************")
print_text(text_array_val,0,10)

In [ ]:
# Removing unnecessary punctuations
PUNCT_TO_REMOVE = "\"$%&'()+,-./;=[\]^_`{|}~"
def remove_punctuation(text):
    return text.translate(str.maketrans('', '', PUNCT_TO_REMOVE))

# Training set
text_array = text_array.apply(lambda text: remove_punctuation(text))
print_text(text_array,0,10)

print("********************************************************************")

# Validation set
text_array_val = text_array_val.apply(lambda text: remove_punctuation(text))
print_text(text_array_val,0,10)

In [ ]:
# print_text(text_array,3550,3555)
print_text(original,9540,9555)

In [ ]:
# Finding length of longest array
maxLen = len(max(text_array,key = lambda text: len(text.split(" "))).split(" "))
print(maxLen)

In [ ]:
u = lambda text: len(text.split(" "))
sentence_lengths = []
for x in text_array:
    sentence_lengths.append(u(x))
print(sorted(sentence_lengths)[-100:])
print(len(sentence_lengths))

<h2>Text pre-processing complete</h2>

In [ ]:
def read_glove_vecs(glove_file):
    with open(glove_file, 'r', encoding="utf8") as f:
        words = set()
        word_to_vec_map = {}
        for line in f:
            line = line.strip().split()
            curr_word = line[0]
            words.add(curr_word)
            word_to_vec_map[curr_word] = np.array(line[1:], dtype=np.float64)
        
        i = 1
        words_to_index = {}
        index_to_words = {}
        for w in sorted(words):
            words_to_index[w] = i
            index_to_words[i] = w
            i = i + 1
    return words_to_index, index_to_words, word_to_vec_map, words

In [ ]:
# We need word_to_index and index_to_word for creating the embedding layer.
word_to_index, index_to_word, word_to_vec_map, vocab = read_glove_vecs('/content/drive/My Drive/Capstone/glove.twitter.27B.100d.txt')

In [ ]:
print(len(word_to_index))
print(len(text_array))

In [ ]:
# Test function for counting the missing vocabulary count
vocab_missing_count = 0
vocab_count = 0
for text in text_array:
    local = 0
    for word in text.split(" "):
        vocab_count += 1
        if not word == "":
            if not word in word_to_vec_map:
                vocab_missing_count += 1
                local += 1

#Printing overall details
print("Total vocabulary count: "+ str(vocab_count))
print("Missing vocabulary count: "+ str(vocab_missing_count))

In [ ]:
# Count of each label in dataset
from collections import Counter

# Printing training set counts for analysis
print("Elements: ",set(labels))
print("Length: ",len(labels))
print(Counter(labels))

print("**************************************************************************")

# Printing validation set counts for analysis
print("Elements: ",set(labels_val))
print("Length: ",len(labels_val))
print(Counter(labels_val))

Elements:  {'NOT', 'OFF'}
Length:  13240
Counter({'NOT': 8840, 'OFF': 4400})
**************************************************************************
Elements:  {'NOT', 'OFF'}
Length:  860
Counter({'NOT': 620, 'OFF': 240})


In [ ]:
Y = []
Y_val = []

# Training set    
for i in range(0,len(labels)):
    if(labels[i] == "OFF"):
        Y.append(0)
    if(labels[i] == "NOT"):
        Y.append(1)

# Test set
for i in range(0,len(labels_val)):
    if(labels_val[i] == "OFF"):
        Y_val.append(0)
    if(labels_val[i] == "NOT"):
        Y_val.append(1)

In [ ]:
Y_target = []
Y_target_val = []

# Training set    
for i in range(0,len(labels_target)):
    if(labels_target[i] == "NA"):
        Y_target.append(0)
    if(labels_target[i] == "TIN"):
        Y_target.append(1)
    if(labels_target[i] == "UNT"):
        Y_target.append(2)

# Test set
for i in range(0,len(labels_target_val)):
    if(labels_target_val[i] == "NA"):
        Y_target_val.append(0)
    if(labels_target_val[i] == "TIN"):
        Y_target_val.append(1)
    if(labels_target_val[i] == "UNT"):
        Y_target_val.append(2)

In [ ]:
# Testing the conversion into integers
for i in range(200,210):
    print(text_array_val[i])
    print(labels_val[i],Y_val[i])
    print(labels_target_val[i],Y_target_val[i])
    print()

In [ ]:
# Verifying train set 
X = np.asarray(list(text_array))
Y = np.asarray(list(Y))
Y_target = np.asarray(list(Y_target))
print(type(X))
print(type(Y))
print(type(Y_target))
print(np.shape(X),np.shape(Y),np.shape(Y_target))

# Verifying validation set
X_val = np.asarray(list(text_array_val))
Y_val = np.asarray(list(Y_val))
Y_target_val = np.asarray(list(Y_target_val))
print(type(X_val))
print(type(Y_val))
print(type(Y_target_val))
print(np.shape(X_val),np.shape(Y_val),np.shape(Y_target_val))

In [ ]:
print(X_val[0])
print(Y_val[0])
print(labels_val[0])
print(Y_target_val[0])
print(labels_target_val[0])

<h2>Model using LSTM with attention</h2>

In [ ]:
import tensorflow as tf
import keras
import keras.backend as K
from keras.layers import LeakyReLU
from keras.models import Model
from keras.layers import Dense, Input, Dropout, LSTM, Activation, Concatenate, Bidirectional, Add, RepeatVector, Dot, BatchNormalization
from keras.layers.embeddings import Embedding
from keras.preprocessing import sequence
from keras.initializers import glorot_uniform
from keras.utils import plot_model

Using TensorFlow backend.


In [ ]:
print(keras.__version__)

In [ ]:
print(tf.__version__)

In [ ]:
K.clear_session()

In [ ]:
# Function to conver sentence to indices using the glove vocab
def sentences_to_indices(X, word_to_index, max_len):
    """
    Converts an array of sentences (strings) into an array of indices corresponding to words in the sentences.

    """
    
    m = X.shape[0]                                   
    X_indices = np.zeros((m,max_len))
    
    for i in range(m):                              
        
        # Convert the ith training sentence in lower case and split is into words.
        sentence_words =(X[i].lower()).split(" ")
        

        j = 0        
        
        for w in sentence_words:
            if j==max_len:
                break
            # Set the (i,j)th entry of X_indices to the index of the correct word.
            if w in word_to_index:
                X_indices[i, j] = word_to_index[w]
                # Increment j to j + 1
                j = j+1
            
    
    return X_indices

In [ ]:
# Test for sentence_to_indices
print("Text: " + text_array[0])
test = sentences_to_indices(text_array[:2],word_to_index,10)
print(test)

In [ ]:
def pretrained_embedding_layer(word_to_vec_map, word_to_index):
    """
    Creates a Keras Embedding() layer and loads in pre-trained GloVe 100-dimensional vectors.

    """
    
    vocab_len = len(word_to_index) + 1                  
    emb_dim = word_to_vec_map["cucumber"].shape[0]      
    
    emb_matrix = np.zeros((vocab_len, emb_dim))
    
    # Set each row "index" of the embedding matrix to be the word vector representation of the "index"th word of the vocabulary
    for word, index in word_to_index.items():
        enc = word_to_vec_map[word]
        # Handling error in glove 
        if not (np.shape(enc)[0] == emb_dim):
            temp = np.zeros((emb_dim,))
            temp[:len(enc)] = word_to_vec_map[word]
            enc = temp
        # Handling of error complete
        emb_matrix[index] = enc

    embedding_layer = Embedding(vocab_len, emb_dim, mask_zero = True, trainable = False)
    embedding_layer.build((None,))
    embedding_layer.set_weights([emb_matrix])
    
    return embedding_layer

In [ ]:
embedding_layer = pretrained_embedding_layer(word_to_vec_map, word_to_index)
print("weights[0][1][3] =", embedding_layer.get_weights()[0][1][3])

In [ ]:
def softmax(x, axis=1):
    """Softmax activation function."""
    ndim = K.ndim(x)
    if ndim == 2:
        return K.softmax(x)
    elif ndim > 2:
        e = K.exp(x - K.max(x, axis=axis, keepdims=True))
        s = K.sum(e, axis=axis, keepdims=True)
        return e / s
    else:
        raise ValueError('Cannot apply softmax to a tensor that is 1D')

In [ ]:
def one_step_attention(a, s_prev):
    """
    Performs one step of attention: Outputs a context vector computed as a dot product of the attention weights.
    """
    s_prev = repeator(s_prev)
    concat = concatenator([a, s_prev])
    e = densor1(concat)
    energies = densor2(e)
    alphas = activator(energies)
    context = dotor([alphas,a])
    
    return context

<h3>Training model to learn features for offensive/non-offensive class</h3>

In [ ]:
repeator = RepeatVector(100)
concatenator = Concatenate(axis=-1)
densor1 = Dense(10, activation = "relu")
densor2 = Dense(1, activation = "relu")
activator = Activation(softmax, name='attention_weights') 
dotor = Dot(axes = 1)

In [ ]:
def Offense_classifier(input_shape, word_to_vec_map, word_to_index):
    """
    Function creating the model's graph.

    """
    s0 = Input(shape=(256,), name='s0')
    s = s0

    # Define sentence_indices as the input of the graph.
    sentence_indices = Input(shape = input_shape, dtype='int32')
    
    # Create the embedding layer pretrained with GloVe Vectors 
    embedding_layer = pretrained_embedding_layer(word_to_vec_map, word_to_index)
    embeddings = embedding_layer(sentence_indices)
    
    embeddings = Dropout(0.1)(embeddings)
    lstm_one = Bidirectional(LSTM(128, return_sequences=True))

    X = lstm_one(embeddings)
    X = Dropout(0.4)(X)

    # *************Attention*******************
    context_conv = []

    post_activation_LSTM_cell = LSTM(256, return_state = True, dropout=0.2, recurrent_dropout=0.2)

    for t in range(input_shape[0]):
    
        context = one_step_attention(X, s)
        
        s, _, c = post_activation_LSTM_cell(context)

        context_conv.append((s))
    # ****************Attention*******************

    conv = keras.layers.Concatenate()(context_conv)
    conv = keras.layers.Reshape((input_shape[0],256))(conv)
    conv = Dropout(0.4)(conv)

    X = keras.layers.GRU(128, return_sequences= False, dropout=0.2, recurrent_dropout=0.2)(conv)

    X = BatchNormalization(momentum=0.99, epsilon=0.001, center=True, scale=True)(X)
    
    # Add dropout with a probability of 0.1
    X = Dropout(0.1)(X)
    
    X = Dense(64,activation='elu',kernel_regularizer=keras.regularizers.l2(0.001))(X)

    X = BatchNormalization(momentum=0.99, epsilon=0.001, center=True, scale=True)(X)

    X = Dense(3,activation='elu',kernel_regularizer=keras.regularizers.l2(0.001))(X)

    X = Dense(128,activation='elu',kernel_regularizer=keras.regularizers.l2(0.01))(X)

    X = Dense(64,activation='elu',kernel_regularizer=keras.regularizers.l2(0.001))(X)

    X = Dense(32,activation='elu',kernel_regularizer=keras.regularizers.l2(0.001))(X)

    X = BatchNormalization(momentum=0.99, epsilon=0.001, center=True, scale=True)(X)

    X = Dense(1,activation='elu',kernel_regularizer=keras.regularizers.l2(0.01))(X)
    
    # Add a sigmoid activation
    X = Activation('sigmoid')(X)
    
    # Create Model instance.
    model = Model(inputs=[s0, sentence_indices], outputs=[X])
    
    
    return model

In [ ]:
model = Offense_classifier((100,), word_to_vec_map, word_to_index)
model.summary()

In [ ]:
model.compile(loss='binary_crossentropy', optimizer="adam", metrics=['accuracy'])

<h4>Finding class weights</h4>

In [ ]:
neg, pos = np.bincount(Y)
total = neg + pos
print('Examples:\n    Total: {}\n    Positive: {} ({:.2f}% of total)\n'.format(
    total, pos, 100 * pos / total))

In [ ]:
class_weight = {}
maxi = max(neg, pos)
weight_for_0 = (maxi / (maxi + neg)) 
weight_for_1 = (maxi / (maxi + pos))

class_weight = {0: weight_for_0, 1: weight_for_1}

print('Weight for class 0: {:.2f}'.format(weight_for_0))
print('Weight for class 1: {:.2f}'.format(weight_for_1))

In [ ]:
# Converting sentence to Indices
X_train_indices = sentences_to_indices(X, word_to_index, 100)
print(np.shape(X_train_indices))
X_val_indices = sentences_to_indices(X_val, word_to_index, 100)
print(np.shape(X_val_indices))

In [ ]:
#Callback for saving weights which can be cchosen after training curves
from keras.callbacks import ModelCheckpoint
checkpoint = ModelCheckpoint(filepath='/content/final_adam.{epoch:03d}.h5',
                                 monitor='val_acc',
                                 verbose=1,
                                 save_weights_only=True,
                                 period=1)

<h4>Splitting Training set to Validation and Train sets</h4> 

In [ ]:
from sklearn.model_selection import train_test_split

In [ ]:
model_train_x, model_val_x, model_train_y, model_val_y = train_test_split(X_train_indices, Y, test_size=0.20, random_state=44)

In [ ]:
print(Counter(Y))
print(Counter(Y_val))

In [ ]:
print(Counter(model_train_y))
print(Counter(model_val_y))

In [ ]:
print(len(model_train_x),len(model_val_x))

In [ ]:
train_s0 = np.zeros((len(model_train_x), 256))
train_s0_val = np.zeros((len(model_val_x), 256))

In [ ]:
print(np.shape(train_s0))
print(np.shape(train_s0_val))

<h3>Splitting end</h3>

In [ ]:
s0 = np.zeros((len(X), 256))
s0_val = np.zeros((len(X_val), 256))

In [ ]:
# plot_model(model, to_file="model.png", show_shapes=False, show_layer_names=True)

In [ ]:
# history = model.fit(
#     [train_s0, model_train_x],
#     model_train_y,
#     batch_size = 128,
#     epochs = 24,
#     validation_data = ([train_s0_val,model_val_x],model_val_y),
#     callbacks = [checkpoint],
#     class_weight = class_weight
# )

<h4>Training Curves</h4>

In [ ]:
history = history
import matplotlib.pyplot as plt
plt.plot(history.history['acc'])
plt.plot(history.history['val_acc'])
plt.title('Model accuracy')
plt.ylabel('Accuracy')
plt.xlabel('Epoch')
plt.legend(['Train', 'Validation'], loc='lower right')
plt.show()

plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.title('Model loss')
plt.ylabel('Loss')
plt.xlabel('Epoch')
plt.legend(['Train', 'Validation'], loc='lower right')
plt.show()

In [ ]:
model.load_weights("/content/drive/MyDrive/offenseval/train_val/final_elu_10.h5")

In [ ]:
# model.save_weights("/content/drive/MyDrive/offenseval/train_val/final_elu_9.h5")

In [ ]:
val_answer = model.predict([train_s0_val, model_val_x])
answer = model.predict([s0_val,X_val_indices])

<h4>Validation set Statistics</h4>

In [ ]:
pred_val = []
count = 0
for i in range(0,len(model_val_x)):

    num = val_answer[i]
    count = count + 1
    if(num > 0.5):
      num = 1
    else:
      num = 0
    pred_val.append(num)

print(count)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=model_val_y, predictions=pred_val)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
from sklearn.metrics import f1_score, classification_report

In [ ]:
print(classification_report(model_val_y, pred_val, target_names=["offensive", "not offensive"], digits=3))

<h4>Test Set Statistics</h4>

In [ ]:
pred = []
sample = df_val_text["tweet"]
count = 0
for i in range(0,len(X_val)):

    num = answer[i]
    if(num > 0.5):
      num = 1
    else:
      num = 0
    pred.append(num)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=Y_val, predictions=pred)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
import seaborn as sns
import matplotlib.pyplot as plt

In [ ]:
figure = plt.figure(figsize=(8, 8))
sns.heatmap(con_mat, annot=True,cmap=plt.cm.viridis,fmt='d', xticklabels=["Offensive","Not Offensive"], yticklabels=["Offensive","Not Offensive"],annot_kws={"size": 14})
plt.tight_layout()
plt.ylabel('True label')
plt.xlabel('Predicted label')
plt.show()

In [ ]:
f1_score(Y_val, pred, average='macro')

In [ ]:
print(classification_report(Y_val, pred, target_names=["offensive", "not offensive"], digits=3))

<h4>Train set analysis. Used for finding incorrect labels using manual error. analysis</h4>

In [ ]:
answer_train = model.predict([s0,X_train_indices])

In [ ]:
# Predicts samples after and before text-preprocessing step. ALso prints correct and predicted labels. 
pred = []
sample = original
count = 0
for i in range(0,len(X)):

    num = answer_train[i]
    lol = num
    if(num > 0.5):
      num = 1
    else:
      num = 0
    pred.append(num)
    if(num != Y[i] and Y[i] == 0 and lol >=0.8):
        print(answer_train[i])
        print("Original label: ",labels[i])
        print("Without pre-processing: ",sample[i])
        print("With pre-processing: ",X[i])
        lol = ""
        count += 1

        if(num == 0):
            lol = "Offensive"
        if(num == 1):
            lol = "Not Offensive"
        print("Predicted: " + lol)
        print()

print(count)

<h3>Training examination</h3>

In [ ]:
import plotly
import plotly.graph_objs as go
import plotly.express as px

In [ ]:
# 3 neuron output
model.layers[-7].name

In [ ]:
cluster_dense_3 = Model(inputs=model.input, outputs=model.layers[-7].output)
cluster_3 = cluster_dense_3.predict([s0,X_train_indices])

In [ ]:
pred_train = []
temp = 0

for i in range(0,len(X)):

    num = answer_train[i]

    if(num >= 0.5):
      num = 1
    else:
      num = 0
    pred_train.append(num)

In [ ]:
flag = []
count = 0

x_ = []
y_ = []
z_ = []


for i in range(0,len(X)):
    count = count + 1
    x_.append(cluster_3[i][2])
    y_.append(cluster_3[i][1])
    z_.append(cluster_3[i][0])

    if( answer_train[i] > 0.3 and answer_train[i] < 0.7 ):
        flag.append(2)
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.3 ):
        flag.append(0)

    if( answer_train[i] >= 0.7 and answer_train[i] < 1 ):
        flag.append(1)


In [ ]:
Counter(flag)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=Y, predictions=pred_train)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
pred_colour = []
for i in range(0,len(flag)):
    if flag[i] == 2:
      pred_colour.append("Neutral")
    if flag[i] == 1:
      pred_colour.append("Not Offensive")
    if flag[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'x':x_, 'y':y_, 'z':z_, 'Labels':pred_colour})

fig = px.scatter_3d(test_df, x='x', y='y', z='z', color='Labels')
fig.update_traces(
    marker={
        'size': 0.6,
        'opacity': 0.7,
        'colorscale' : 'Oryel',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 750, height = 500)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))

<h3>Traning examination end</h3>

<h1>CLUSTERING</h1>

<h3>GRU layer</h3>

In [ ]:
model.layers[-11].name

'batch_normalization_1'

In [ ]:
cluster_gru = Model(inputs=model.input, outputs=model.layers[-11].output)
cl_gru = cluster_gru.predict([s0,X_train_indices])

In [ ]:
# Used for finding the correct cluster corresponding to each class.
flag_gru = []
count = 0

x_gru = []
y_gru = []
z_gru = []


for i in range(0,len(X)):
    count = count + 1
    x_gru.append(cl_gru[i][0])
    y_gru.append(cl_gru[i][1])
    z_gru.append(cl_gru[i][2])

    if( answer_train[i] > 0.28 and answer_train[i] < 0.9 ):
        flag_gru.append(2)
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.28 ):
        flag_gru.append(0)

    if( answer_train[i] >= 0.9 and answer_train[i] < 1 ):
        flag_gru.append(1)

print(count)

In [ ]:
from sklearn.cluster import KMeans

In [ ]:
kmeans_gru = KMeans(n_clusters=3, random_state=44).fit(cl_gru)
y_kmeans_gru = kmeans_gru.predict(cl_gru)

In [ ]:
Counter(y_kmeans_gru)

In [ ]:
Counter(flag_gru)

In [ ]:
# 1 index values are offensive
# 0 index values are not offensive
# 2 index values are neutral

count = 0
for i in range(0,len(flag_gru)):
      if flag_gru[i] == 0 and y_kmeans_gru[i] == 1:
        count = count + 1
print(count)

In [ ]:
# Used for correctly labelling the cluster corresponding to each class.
for i in range(0,len(flag_gru)):
    if(y_kmeans_gru[i] == 0):
      y_kmeans_gru[i] = 1
    elif(y_kmeans_gru[i] == 1):
      y_kmeans_gru[i] = 0
    else:
      y_kmeans_gru[i] = 2

In [ ]:
flag_gru = []
count = 0

x_gru = []
y_gru = []
z_gru = []


for i in range(0,len(X)):
    count = count + 1
    x_gru.append(cl_gru[i][0])
    y_gru.append(cl_gru[i][1])
    z_gru.append(cl_gru[i][2])

    if( answer_train[i] > 0.3 and answer_train[i] < 0.7 ):
        flag_gru.append(2) # Neutral Samples
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.3 ):
        flag_gru.append(0) # Offensive samples

    if( answer_train[i] >= 0.7 and answer_train[i] < 1 ):
        flag_gru.append(1) # Non-offensive samples

print(count)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=flag_gru, predictions=y_kmeans_gru)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
import sklearn
print(sklearn.metrics.classification_report(flag_gru, y_kmeans_gru, output_dict=False, digits=3))

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
from scipy.spatial.distance import cosine

In [ ]:
centers_gru = kmeans_gru.cluster_centers_

In [ ]:
svns_off = []
for i in range(0,len(flag_gru)):
    off = cosine(cl_gru[i], centers_gru[1])/2
    svns_off.append(1-off)
print(len(svns_off))

In [ ]:
svns_noff = []
for i in range(0,len(flag_gru)):
    noff = cosine(cl_gru[i], centers_gru[0])/2
    svns_noff.append(1-noff)
print(len(svns_noff))

In [ ]:
svns_neu = []
for i in range(0,len(flag_gru)):
    neu = cosine(cl_gru[i], centers_gru[2])/2
    svns_neu.append(1-neu)
print(len(svns_neu))

In [ ]:
import plotly
import plotly.graph_objs as go
import plotly.express as px

In [ ]:
pred_colour = []
for i in range(0,len(y_kmeans_gru)):
    if y_kmeans_gru[i] == 2:
      pred_colour.append("Neutral")
    if y_kmeans_gru[i] == 1:
      pred_colour.append("Not Offensive")
    if y_kmeans_gru[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'SVNS Offensive':svns_off, 'SVNS Not Offensive':svns_noff, 'SVNS Neutral':svns_neu, 'Labels:':pred_colour})

fig = px.scatter_3d(test_df, x='SVNS Offensive', y='SVNS Not Offensive', z='SVNS Neutral', color='Labels:')
fig.update_traces(
    marker={
        'size': 1,
        'opacity': 1,
        'colorscale' : 'viridis',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 850, height = 750)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))

<p> GMM model </p>

In [ ]:
from sklearn.mixture import GaussianMixture

In [ ]:
gmm_gru = GaussianMixture(n_components=3, random_state = 44).fit(cl_gru)

In [ ]:
mean_gru = gmm_gru.means_
cov_gru = gmm_gru.covariances_
print(np.shape(mean_gru))
print(np.shape(cov_gru))

In [ ]:
labels_gru = gmm_gru.predict(cl_gru)

In [ ]:
# Used for finding the correct cluster corresponding to each class.
flag_gru = []
count = 0

x_gru = []
y_gru = []
z_gru = []


for i in range(0,len(X)):
    count = count + 1
    x_gru.append(cl_gru[i][0])
    y_gru.append(cl_gru[i][1])
    z_gru.append(cl_gru[i][2])

    if( answer_train[i] > 0.28 and answer_train[i] < 0.9 ):
        flag_gru.append(2)
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.28 ):
        flag_gru.append(0)

    if( answer_train[i] >= 0.9 and answer_train[i] < 1 ):
        flag_gru.append(1)

print(count)

In [ ]:
Counter(flag_gru)

In [ ]:
# 0 index values are offensive
# 1 index values are not offensive
# 2 index values are neutral

count = 0
for i in range(0,len(flag_gru)):
      if flag_gru[i] == 0 and labels_gru[i] == 0:
        count = count + 1
print(count)

In [ ]:
for i in range(0,len(flag_gru)):
    if(labels_gru[i] == 0):
      labels_gru[i] = 0
    elif(labels_gru[i] == 1):
      labels_gru[i] = 1
    else:
      labels_gru[i] = 2

In [ ]:
flag_gru = []
count = 0

x_gru = []
y_gru = []
z_gru = []


for i in range(0,len(X)):
    count = count + 1
    x_gru.append(cl_gru[i][0])
    y_gru.append(cl_gru[i][1])
    z_gru.append(cl_gru[i][2])

    if( answer_train[i] > 0.3 and answer_train[i] < 0.7 ):
        flag_gru.append(2) # Neutral Samples
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.3 ):
        flag_gru.append(0) # Offensive Samples

    if( answer_train[i] >= 0.7 and answer_train[i] < 1 ):
        flag_gru.append(1) # Non-Offensive Samples

print(count)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=flag_gru, predictions=labels_gru)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
import sklearn
print(sklearn.metrics.classification_report(flag_gru, labels_gru, output_dict=False, digits=3))

In [ ]:
prob_gru = gmm_gru.predict_proba(cl_gru)
prob_gru = prob_gru.T

In [ ]:
pred_colour = []
for i in range(0,len(y_kmeans_gru)):
    if labels_gru[i] == 2:
      pred_colour.append("Neutral")
    if labels_gru[i] == 1:
      pred_colour.append("Not Offensive")
    if labels_gru[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'SVNS Offensive':prob_gru[0], 'SVNS Non Offensive':prob_gru[1], 'SVNS Neutral':prob_gru[2], 'Labels:':pred_colour})

fig = px.scatter_3d(test_df, x='SVNS Offensive', y='SVNS Non Offensive', z='SVNS Neutral', color='Labels:')
fig.update_traces(
    marker={
        'size': 1.8,
        'opacity': 1,
        'colorscale' : 'viridis',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 850, height = 750)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))

<h3>Dense 3 layer</h3>

In [ ]:
from sklearn.preprocessing import normalize

In [ ]:
cl_norm = normalize(cluster_3, norm='l2', axis=1)

In [ ]:
# Used for finding the correct cluster corresponding to each class.
flag_3 = []
count = 0

x_ = []
y_ = []
z_ = []


for i in range(0,len(X)):
    count = count + 1
    x_.append(cl_norm[i][0])
    y_.append(cl_norm[i][1])
    z_.append(cl_norm[i][2])

    if( answer_train[i] > 0.28 and answer_train[i] < 0.9 ):
        flag_3.append(2)
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.28 ):
        flag_3.append(0)

    if( answer_train[i] >= 0.9 and answer_train[i] < 1 ):
        flag_3.append(1)

print(count)

In [ ]:
kmeans_3 = KMeans(n_clusters=3, random_state=44).fit(cl_norm)
y_kmeans_3 = kmeans_3.predict(cl_norm)

In [ ]:
Counter(y_kmeans_3)

In [ ]:
Counter(flag_3)

In [ ]:
# 1 index values are offensive
# 0 index values are not offensive
# 2 index values are neutral

count = 0
for i in range(0,len(flag_3)):
      if flag_3[i] == 1 and y_kmeans_3[i] == 0:
        count = count + 1
print(count)

In [ ]:
for i in range(0,len(flag_3)):
    if(y_kmeans_3[i] == 0):
      y_kmeans_3[i] = 1
    elif(y_kmeans_3[i] == 1):
      y_kmeans_3[i] = 0
    else:
      y_kmeans_3[i] = 2

In [ ]:
flag_3 = []
count = 0

x_ = []
y_ = []
z_ = []


for i in range(0,len(X)):
    count = count + 1
    x_.append(cl_norm[i][2])
    y_.append(cl_norm[i][1])
    z_.append(cl_norm[i][0])

    if( answer_train[i] > 0.3 and answer_train[i] < 0.7 ):
        flag_3.append(2) # Neutral Samples
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.3 ):
        flag_3.append(0) # Offensive Samples

    if( answer_train[i] >= 0.7 and answer_train[i] < 1 ):
        flag_3.append(1) # Non offensive Samples

print(count)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=flag_3, predictions=y_kmeans_3)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
import sklearn
print(sklearn.metrics.classification_report(flag_3, y_kmeans_3, output_dict=False, digits=3))

<p>Transition phase</p>

In [ ]:
pred_colour = []
for i in range(0,len(y_kmeans_gru)):
    if y_kmeans_3[i] == 2:
      pred_colour.append("Neutral")
    if y_kmeans_3[i] == 1:
      pred_colour.append("Not Offensive")
    if y_kmeans_3[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'X':x_, 'Y':y_, 'Z':z_, 'Labels:':pred_colour})

fig = px.scatter_3d(test_df, x='X', y='Y', z='Z', color='Labels:')
fig.update_traces(
    marker={
        'size': 1,
        'opacity': 1,
        'colorscale' : 'viridis',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 850, height = 750)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))

<p>Original predictions</p>

In [ ]:
pred_colour = []
for i in range(0,len(y_kmeans_gru)):
    if pred_train[i] == 1:
      pred_colour.append("Not Offensive")
    if pred_train[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'X':x_, 'Y':y_, 'Z':z_, 'Labels:':pred_colour})

fig = px.scatter_3d(test_df, x='X', y='Y', z='Z', color='Labels:')
fig.update_traces(
    marker={
        'size': 1,
        'opacity': 1,
        'colorscale' : 'rainbow',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 850, height = 750)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))

<h4>End of transition capture</h4> 

<h4>SVNS Values</h4>

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
from scipy.spatial.distance import cosine

In [ ]:
centers_3 = kmeans_3.cluster_centers_

In [ ]:
svns_off = []
for i in range(0,len(flag_3)):
    off = cosine(cl_norm[i], centers_3[1])/2
    svns_off.append(1-off)
print(len(svns_off))

In [ ]:
svns_noff = []
for i in range(0,len(flag_3)):
    noff = cosine(cl_norm[i], centers_3[0])/2
    svns_noff.append(1-noff)
print(len(svns_noff))

In [ ]:
svns_neu = []
for i in range(0,len(flag_3)):
    neu = cosine(cl_norm[i], centers_3[2])/2
    svns_neu.append(1-neu)
print(len(svns_neu))

In [ ]:
pred_colour = []
for i in range(0,len(y_kmeans_gru)):
    if y_kmeans_3[i] == 2:
      pred_colour.append("Neutral")
    if y_kmeans_3[i] == 1:
      pred_colour.append("Not Offensive")
    if y_kmeans_3[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'SVNS Offensive':svns_off, 'SVNS Not Offensive':svns_noff, 'SVNS Neutral':svns_neu, 'Labels:':pred_colour})

fig = px.scatter_3d(test_df, x='SVNS Offensive', y='SVNS Not Offensive', z='SVNS Neutral', color='Labels:')
fig.update_traces(
    marker={
        'size': 1,
        'opacity': 1,
        'colorscale' : 'viridis',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 850, height = 750)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))

<p> GMM model </p>

In [ ]:
gmm_3 = GaussianMixture(n_components=3, random_state = 44).fit(cl_norm)

In [ ]:
mean_norm = gmm_3.means_
cov_norm = gmm_3.covariances_
print(np.shape(mean_norm))
print(np.shape(cov_norm))

In [ ]:
labels_norm = gmm_3.predict(cl_norm)

In [ ]:
# Used for finding the correct cluster corresponding to each class.
flag_3 = []
count = 0

x_ = []
y_ = []
z_ = []


for i in range(0,len(X)):
    count = count + 1
    x_.append(cl_norm[i][2])
    y_.append(cl_norm[i][1])
    z_.append(cl_norm[i][0])

    if( answer_train[i] > 0.28 and answer_train[i] < 0.9 ):
        flag_3.append(2)
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.28 ):
        flag_3.append(0)

    if( answer_train[i] >= 0.9 and answer_train[i] < 1 ):
        flag_3.append(1)

print(count)

In [ ]:
Counter(labels_norm)

In [ ]:
Counter(flag_3)

In [ ]:
# 0 index values are offensive
# 1 index values are not offensive
# 2 index values are neutral

count = 0
for i in range(0,len(flag_3)):
      if flag_3[i] == 1 and labels_norm[i] == 1:
        count = count + 1
print(count)

In [ ]:
for i in range(0,len(flag_3)):
    if(labels_norm[i] == 0):
      labels_norm[i] = 0
    elif(labels_norm[i] == 1):
      labels_norm[i] = 1
    else:
      labels_norm[i] = 2

In [ ]:
flag_3 = []
count = 0

x_ = []
y_ = []
z_ = []


for i in range(0,len(X)):
    count = count + 1
    x_.append(cl_norm[i][2])
    y_.append(cl_norm[i][1])
    z_.append(cl_norm[i][0])

    if( answer_train[i] > 0.3 and answer_train[i] < 0.7 ):
        flag_3.append(2) # Neutral Samples
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.3 ):
        flag_3.append(0) # Offensive Samples

    if( answer_train[i] >= 0.7 and answer_train[i] < 1 ):
        flag_3.append(1) # Non-offensive Samples

print(count)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=flag_3, predictions=labels_norm)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
import sklearn
print(sklearn.metrics.classification_report(flag_3, labels_norm, output_dict=False, digits=3))

In [ ]:
prob_norm = gmm_3.predict_proba(cl_norm)
prob_norm = prob_norm.T

In [ ]:
pred_colour = []
for i in range(0,len(y_kmeans_gru)):
    if labels_norm[i] == 2:
      pred_colour.append("Neutral")
    if labels_norm[i] == 1:
      pred_colour.append("Not Offensive")
    if labels_norm[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'SVNS Offensive':prob_norm[0], 'SVNS Not Offensive':prob_norm[1], 'SVNS Neutral':prob_norm[2], 'Labels:':pred_colour})

fig = px.scatter_3d(test_df, x='SVNS Offensive', y='SVNS Not Offensive', z='SVNS Neutral', color='Labels:')
fig.update_traces(
    marker={
        'size': 1.5,
        'opacity': 1,
        'colorscale' : 'viridis',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 850, height = 750)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))

<h3>Dense 3 layer end</h3>

<h3>Batch Norm layer</h3>

In [ ]:
model.layers[-3].name

In [ ]:
# layer_d = model.layers[-7].output
# plt_val = BatchNormalization(momentum=0.99, epsilon=0.001, center=True, scale=True)(layer_d)
cluster_32 = Model(inputs=model.input, outputs=model.layers[-3].output)
cl_32 = cluster_32.predict([s0,X_train_indices])

In [ ]:
# Used for finding the correct cluster corresponding to each class.
flag_32 = []
count = 0

x_32 = []
y_32 = []
z_32 = []


for i in range(0,len(X)):
    count = count + 1
    x_32.append(cl_32[i][0])
    y_32.append(cl_32[i][1])
    z_32.append(cl_32[i][2])

    if( answer_train[i] > 0.28 and answer_train[i] < 0.9 ):
        flag_32.append(2)
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.28 ):
        flag_32.append(0)

    if( answer_train[i] >= 0.9 and answer_train[i] < 1 ):
        flag_32.append(1)

print(count)

In [ ]:
kmeans_32 = KMeans(n_clusters=3, random_state=44).fit(cl_32)
y_kmeans_32 = kmeans_32.predict(cl_32)

In [ ]:
Counter(y_kmeans_32)

In [ ]:
Counter(flag_32)

In [ ]:
# 1 index values are offensive
# 0 index values are not offensive
# 2 index values are neutral

count = 0
for i in range(0,len(y_kmeans_32)):
      if flag_32[i] == 0 and y_kmeans_32[i] == 1:
        count = count + 1
print(count)

In [ ]:
for i in range(0,len(y_kmeans_32)):
    if(y_kmeans_32[i] == 0):
      y_kmeans_32[i] = 1
    elif(y_kmeans_32[i] == 1):
      y_kmeans_32[i] = 0
    else:
      y_kmeans_32[i] = 2

In [ ]:
flag_32 = []
count = 0

x_32 = []
y_32 = []
z_32 = []


for i in range(0,len(X)):
    count = count + 1
    x_32.append(cl_32[i][0])
    y_32.append(cl_32[i][1])
    z_32.append(cl_32[i][2])

    if( answer_train[i] > 0.3 and answer_train[i] < 0.7 ):
        flag_32.append(2) # Neutral Samples 
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.3 ):
        flag_32.append(0) # Offensive Samples

    if( answer_train[i] >= 0.7 and answer_train[i] < 1 ):
        flag_32.append(1) # Non-offensive Samples

print(count)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=flag_32, predictions=y_kmeans_32)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
import sklearn
print(sklearn.metrics.classification_report(flag_32, y_kmeans_32, output_dict=False, digits=3))

<h3>SVNS Values</h3>

In [ ]:
centers_32 = kmeans_32.cluster_centers_

In [ ]:
svns_off = []
for i in range(0,len(flag_32)):
    off = cosine(cl_32[i], centers_32[1])/2
    svns_off.append(1-off)
print(len(svns_off))

In [ ]:
svns_noff = []
for i in range(0,len(flag_32)):
    noff = cosine(cl_32[i], centers_32[0])/2
    svns_noff.append(1-noff)
print(len(svns_noff))

In [ ]:
svns_neu = []
for i in range(0,len(flag_32)):
    neu = cosine(cl_32[i], centers_32[2])/2
    svns_neu.append(1-neu)
print(len(svns_neu))

In [ ]:
pred_colour = []
for i in range(0,len(y_kmeans_gru)):
    if y_kmeans_32[i] == 2:
      pred_colour.append("Neutral")
    if y_kmeans_32[i] == 1:
      pred_colour.append("Not Offensive")
    if y_kmeans_32[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'SVNS Offensive':svns_off, 'SVNS Not Offensive':svns_noff, 'SVNS Neutral':svns_neu, 'Labels:':pred_colour})

fig = px.scatter_3d(test_df, x='SVNS Offensive', y='SVNS Not Offensive', z='SVNS Neutral', color='Labels:')
fig.update_traces(
    marker={
        'size': 1,
        'opacity': 1,
        'colorscale' : 'viridis',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 850, height = 750)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))

<p> GMM Model </p>

In [ ]:
gmm_32 = GaussianMixture(n_components=3, random_state = 44).fit(cl_32)

In [ ]:
mean_32 = gmm_32.means_
cov_32 = gmm_32.covariances_
print(np.shape(mean_32))
print(np.shape(cov_32))

In [ ]:
labels_32 = gmm_32.predict(cl_32)

In [ ]:
# Used for finding the correct cluster corresponding to each class.
flag_32 = []
count = 0

x_32 = []
y_32 = []
z_32 = []


for i in range(0,len(X)):
    count = count + 1
    x_32.append(cl_32[i][0])
    y_32.append(cl_32[i][1])
    z_32.append(cl_32[i][2])

    if( answer_train[i] > 0.28 and answer_train[i] < 0.9 ):
        flag_32.append(2)
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.28 ):
        flag_32.append(0)

    if( answer_train[i] >= 0.9 and answer_train[i] < 1 ):
        flag_32.append(1)

print(count)

In [ ]:
Counter(flag_32)

In [ ]:
# 2 index values are offensive
# 1 index values are not offensive
# 0 index values are neutral

count = 0
for i in range(0,len(flag_32)):
      if flag_32[i] == 0 and labels_32[i] == 2:
        count = count + 1
print(count)

In [ ]:
for i in range(0,len(flag_32)):
    if(labels_32[i] == 0):
      labels_32[i] = 2
    elif(labels_32[i] == 1):
      labels_32[i] = 1
    else:
      labels_32[i] = 0

In [ ]:
flag_32 = []
count = 0

x_32 = []
y_32 = []
z_32 = []


for i in range(0,len(X)):
    count = count + 1
    x_32.append(cl_32[i][0])
    y_32.append(cl_32[i][1])
    z_32.append(cl_32[i][2])

    if( answer_train[i] > 0.3 and answer_train[i] < 0.7 ):
        flag_32.append(2)
    
    if( answer_train[i] > 0 and answer_train[i] <= 0.3 ):
        flag_32.append(0)

    if( answer_train[i] >= 0.7 and answer_train[i] < 1 ):
        flag_32.append(1)

print(count)

In [ ]:
con_mat = tf.math.confusion_matrix(labels=flag_32, predictions=labels_32)
con_mat = tf.Session().run(con_mat)
con_mat_norm = np.around(con_mat.astype('float') / con_mat.sum(axis=1)[:, np.newaxis], decimals=2)
print(con_mat)

In [ ]:
import sklearn
print(sklearn.metrics.classification_report(flag_32, labels_32, output_dict=False, digits=3))

In [ ]:
prob_32 = gmm_32.predict_proba(cl_32)
prob_32 = prob_32.T

In [ ]:
pred_colour = []
for i in range(0,len(y_kmeans_gru)):
    if labels_32[i] == 2:
      pred_colour.append("Neutral")
    if labels_32[i] == 1:
      pred_colour.append("Not Offensive")
    if labels_32[i] == 0:
      pred_colour.append("Offensive")

test_df = pd.DataFrame({'SVNS Offensive':prob_32[2], 'SVNS Not Offensive':prob_32[1], 'SVNS Neutral':prob_32[0], 'Labels:':pred_colour})

fig = px.scatter_3d(test_df, x='SVNS Offensive', y='SVNS Not Offensive', z='SVNS Neutral', color='Labels:')
fig.update_traces(
    marker={
        'size': 1.5,
        'opacity': 1,
        'colorscale' : 'viridis',
    }
)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(width = 850, height = 750)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))